# Using the Analytics Engine (AE) to access station data
This notebook illustrates how to access the historical meteorological station data at stations of interest throughout WECC.

To execute a given 'cell' of this notebook, place the cursor in the cell and press the 'play' icon, or simply press shift+enter together. Some cells will take longer to run, and you will see a [$\ast$] to the left of the cell while AE is still working.

**Intended Application**: As a user, I want to **<span style="color:#FF0000">access the historical meteorological station data</span>** that is used to localize the dynamically downscaled WRF data in demand forecast modeling through:
1. Accessing and visualizing historical data at a station of interest
2. Exporting the historical data at a station of interest in a reader-friendly format

**Runtime**: With the default settings, this notebook takes approximately **less than 1 minute** to run from start to finish. Modifications to selections may increase the runtime. 

### Step 0: Set-up

In [1]:
import climakitae as ck
import climakitaegui as ckg
import pandas as pd
import xarray as xr
import panel as pn
pn.extension()

from climakitae.util.utils import read_csv_file

### Step 1: Select a station of interest

First, we'll read in a station file of all the HadISD stations currently hooked up to the Analytics Engine. 

In [2]:
# Import stations names and coordinates file
stations = "data/hadisd_stations.csv"
stations_df = read_csv_file(stations)
stations_df

Unnamed: 0 state                                         station  \
0            0    CA                Bakersfield Meadows Field (KBFL)   
1            1    CA                              Blythe Asos (KBLH)   
2            2    CA        Burbank-Glendale-Pasadena Airport (KBUR)   
3            3    CA                          Needles Airport (KEED)   
4            4    CA    Fresno Yosemite International Airport (KFAT)   
5            5    CA                  Imperial County Airport (KIPL)   
6            6    CA        Los Angeles International Airport (KLAX)   
7            7    CA               Long Beach Daugherty Field (KLGB)   
8            8    CA              Modesto City-County Airport (KMOD)   
9            9    CA                  San Diego Miramar Wscmo (KNKX)   
10          10    CA      Oakland Metro International Airport (KOAK)   
11          11    CA            Oxnard Ventura County Airport (KOXR)   
12          12    CA            Palm Springs Regional Airport (KPSP)   
13          13    CA              Riverside Municipal Airport (KRAL)   
14          14    CA              Red Bluff Municipal Airport (KRBL)   
15          15    CA             Sacramento Executive Airport (KSAC)   
16          16    CA                San Diego Lindbergh Field (KSAN)   
17          17    CA          Santa Barbara Municipal Airport (KSBA)   
18          18    CA                  San Luis Obispo Airport (KSBP)   
19          19    CA                  Gillespie Field Airport (KSEE)   
20          20    CA      San Francisco International Airport (KSFO)   
21          21    CA           San Jose International Airport (KSJC)   
22          22    CA             Santa Ana John Wayne Airport (KSNA)   
23          23    CA          Desert Resorts Regional Airport (KTRM)   
24          24    CA                  Ukiah Municipal Airport (KUKI)   
25          25    CA            Lancaster William J Fox Field (KWJF)   
26          26    CA                    Arcata Eureka Airport (KACV)   
27          27    CA                         Stockton Airport (KSCK)   
28          28    CA                          Redding Airport (KRDD)   
29          29    CA  Merced Municipal Airport MacReady Field (KMCE)   
30          30    NV           McCarran International Airport (KLAS)   
31          31    CA          Downtown Los Angeles USC Campus (KCQT)   
32          32    CA            Ontario International Airport (KONT)   

               city    ID      LAT_Y       LON_X   station id  elevation  
0       Bakersfield  KBFL  35.434240 -119.055240  72384023155      149.3  
1            Blythe  KBLH  33.618760 -114.714510  74718823158      120.4  
2           Burbank  KBUR  34.199660 -118.365430  72288023152      222.7  
3           Needles  KEED  34.767830 -114.618420  72380523179      270.6  
4            Fresno  KFAT  36.779990 -119.720160  72389093193      101.9  
5          Imperial  KIPL  32.834640 -115.576560  74718599999      -16.0  
6               Lax  KLAX  33.938160 -118.386600  72295023174       29.7  
7        Long Beach  KLGB  33.811770 -118.147180  72297023129       10.2  
8           Modesto  KMOD  37.625440 -120.954920  72492623258       26.6  
9           Miramar  KNKX  32.866667 -117.133333  99999993107      145.7  
10          Oakland  KOAK  37.717800 -122.233010  72493023230        1.5  
11           Oxnard  KOXR  34.200120 -119.204170  72392793110       11.9  
12     Palm Springs  KPSP  33.822160 -116.504330  72286899999      145.0  
13        Riverside  KRAL  33.952820 -117.435230  72286903171      249.0  
14        Red Bluff  KRBL  40.151860 -122.254780  72591024216      108.1  
15       Sacramento  KSAC  38.506590 -121.496040  72483023232        5.9  
16        San Diego  KSAN  32.733600 -117.183100  72290023188        4.6  
17    Santa Barbara  KSBA  34.424100 -119.842490  72392523190        2.5  
18  San Luis Obispo  KSBP  35.238150 -120.644060  72289799999       65.0  
19           Santee  KSEE  32.826111 -116.972500  72290

The easiest way to access a station is to use the `ID` of the station. We'll demonstrate with "KSAC" for Sacramento Executive Airport. If you are looking to export multiple stations, the following cell is the only one you need to modify in this notebook. 

In [3]:
my_station = 'KSAC' # set to any station of interest

In [4]:
station_id = str(stations_df[stations_df['ID'] == my_station]['station id'].values[0])
filepaths = ["s3://cadcat/hadisd/HadISD_{}.zarr".format(s_id) for s_id in [station_id]]
filepaths # check the filepath

['s3://cadcat/hadisd/HadISD_72483023232.zarr']

### Step 2: Retrieve the station data from the s3 bucket
Here we'll use a handy function to access the data. You don't have to change anything -- this step is set-up with the filepath we identified above.

In [5]:
obs_ds = xr.open_mfdataset(
    filepaths,
    engine="zarr",
    consolidated=False,
    parallel=True,
    backend_kwargs=dict(storage_options={"anon": True}),
)

obs_ds

<xarray.Dataset> Size: 6MB
Dimensions:    (time: 384240)
Coordinates:
    elevation  float64 8B ...
    latitude   float64 8B ...
    longitude  float64 8B ...
  * time       (time) datetime64[ns] 3MB 1980-01-01 ... 2023-10-31T23:00:00
Data variables:
    tas        (time) float64 3MB dask.array<chunksize=(384240,), meta=np.ndarray>

Next, we'll load the data into memory, which will help with both visualizing the data and exporting it in Step 3. 

In [6]:
obs_ds = ck.load(obs_ds)

Processing data to read 5.86 MB of data into memory... Complete!


In [7]:
ckg.view(obs_ds)

:Curve   [time]   (Dry bulb air temperature at screen height (~2m))

### Step 3: Export the station into csv format for ease of use
To export into a reader-friendly format, we'll run the next cell. You don't need to modify anything here - it's set-up to automatically identify the station we have been using (KSAC, as the default). 

In [8]:
filename = 'HadISD_{}'.format(station_id)
ck.export(obs_ds, filename, "csv")

/home/jovyan/src/climakitae/climakitae/core/data_export.py:111: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.
  est_file_size = prod(data.dims.values()) * chars_per_line
<frozen _collections_abc>:913: FutureWarning: The return type of `Dataset.dims` will be changed to return a set of dimension names in future, in order to be more consistent with `DataArray.dims`. To access a mapping from dimension names to lengths, please use `Dataset.sizes`.


Exporting specified data to CSV...
NOTE: File metadata will be written in /home/jovyan/cae-notebooks/collaborative/DFU/HadISD_72483023232_metadata.txt. We recommend you download this along with the CSV for your records.
Saved! You can find your file(s) in the panel to the left and download to your local machine from there.


### Step 4: Optional "fast access" mode
We provide this step where all of the above cells are condensed into a single run for faster access. We've set `my_station` to a different station this time, to demonstrate. 

In [ ]:
# read in station data
stations = "data/hadisd_stations.csv"
stations_df = read_csv_file(stations)

# identify station to export
my_station = 'KACV' # set to any station of interst

# retrieves data
station_id = str(stations_df[stations_df['ID'] == my_station]['station id'].values[0])
filepaths = ["s3://cadcat/hadisd/HadISD_{}.zarr".format(s_id) for s_id in [station_id]]
obs_ds = xr.open_mfdataset(
    filepaths,
    engine="zarr",
    consolidated=False,
    parallel=True,
    backend_kwargs=dict(storage_options={"anon": True}),
)

# load data in for export
obs_ds = ck.load(obs_ds)

# export
filename = 'HadISD_{}'.format(station_id)
ck.export(obs_ds, filename, "csv")